# Importation 

In [1]:
import os
os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"] = "0"

In [2]:
import numpy as np 
import pandas as pd 
import seaborn as sns
from sklearn import model_selection

import cv2
import SimpleITK as sitk
from ipywidgets import interact, fixed
from tqdm import tqdm 
import matplotlib.pyplot as plt
from PIL import Image


import torch
from torch import nn
import torch.nn.functional as F
import torch.optim as optim
from transformers import get_linear_schedule_with_warmup
import albumentations as A 

from torch.autograd import Variable
from math import exp

from collections import OrderedDict
from sklearn.model_selection import train_test_split
import gc ,random 


from loss.ssim import * 
from models.UNet import *
from datasets.merging_dataset import * 

In [3]:
# SEED Everything 

SEED = 42
random.seed(SEED)
np.random.seed(SEED)
torch.manual_seed(SEED)
torch.cuda.manual_seed(SEED)
torch.backends.cudnn.deterministic = True

# Model : UNet

Original paper by Olaf Ronneberger, Philipp Fischer, Thomas Brox: https://arxiv.org/abs/1505.04597

![](https://malekmechergui.github.io/work/Image1.png)

# Engine

### Loss Function

In [4]:
def loss_fn (img1, img2):
    return 1-SSIM()(img1, img2)

### Train function

In [5]:
def train_fn(data_loader, model, optimizer, scheduler):
    
    model.train()
   
    tr_loss = 0 
    counter = 0 
    
    if verbose : 
        tk0 = tqdm(enumerate(data_loader), total=len(data_loader))
    else : 
        tk0 = enumerate(data_loader)
    for bi, d in tk0 :  
    

        y = d["HR"]
        y = y.to(device, dtype=torch.float)
        x = d["LR"]
        x = x.to(device, dtype=torch.float)
        x = x.unsqueeze(1)

        y_hat  = model(x) 
        y = y.unsqueeze(1)
      
        loss = loss_fn(y_hat, y) 
        optimizer.zero_grad() 
       
        tr_loss += loss.item()
        counter +=1 
        
        loss.backward()  
        optimizer.step() 
        
        
    return tr_loss/counter

### Evalution function

In [6]:
def eval_fn(data_loader, model):
    model.eval()
    tr_loss = 0
    counter = 0
    
    
    if verbose : 
        tk0 = tqdm(enumerate(data_loader), total=len(data_loader))
    else : 
        tk0 = enumerate(data_loader)
    with torch.no_grad():
        
        for bi, d in tk0 : 
            
            y = d["HR"] 
            y = y.to(device, dtype=torch.float)
            x = d["LR"]
            x = x.to(device, dtype=torch.float)
            x = x.unsqueeze(1)
            y_hat  = model(x) 
            y = y.unsqueeze(1)
            
            loss = loss_fn(y_hat, y) 
        

            tr_loss += loss.item()
            counter +=1 

            
        return tr_loss/counter 

### Run function

In [7]:
def run(model,EPOCHS, train_dataset, valid_dataset, TRAIN_BATCH_SIZE, VALID_BATCH_SIZE):
    
    train_data_loader = torch.utils.data.DataLoader(
        train_dataset,
        shuffle = True , 
        batch_size=TRAIN_BATCH_SIZE,
        num_workers=8
    )
    
    
    valid_data_loader = torch.utils.data.DataLoader(
        valid_dataset,
        batch_size=VALID_BATCH_SIZE,
        num_workers=4
    )

    


    num_train_steps = int(len(train_data_loader)) * EPOCHS
    optimizer = optim.Adam(model.parameters(), lr=LR)   
    scheduler = get_linear_schedule_with_warmup(
        optimizer,
        num_warmup_steps=0,
        num_training_steps=num_train_steps
    )
    train_loss =  []
    val_loss = []
    best_validation_dsc = 1.0
    patience = 0 
    
    for epoch in range(EPOCHS):
        if verbose : 
            print(f'--------- Epoch {epoch} ---------')
        elif epoch % 10 == 0 : 
            print(f'--------- Epoch {epoch} ---------')
       
        tr_loss=train_fn(train_data_loader, model, optimizer, scheduler)
        train_loss.append(tr_loss)
        
        if verbose : 
            print(f" train_loss  = {tr_loss}")
        elif epoch % 10 == 0 : 
            print(f" train_loss  = {tr_loss}")
        
        val = eval_fn(valid_data_loader, model)
        val_loss.append(val)
        
        if verbose : 
            print(f" val_loss  = {val}")
        elif epoch % 10 == 0 :
            print(f" val_loss  = {val}")
        
        if val < best_validation_dsc : 
            best_validation_dsc =val 
            patience = 0 
            torch.save(model.state_dict(), 'UNet.pt')
        else : 
            patience +=1
        
        if patience>20 : 
            print(f'Eraly Stopping on Epoch {epoch}')
            print(f'Best Loss =  {best_validation_dsc}')
            break
        scheduler.step()
        
    model.load_state_dict(torch.load('UNet.pt'), strict=False)
    return val_loss,train_loss

# Model Training (on Left hippocampus)

In [8]:
data = pd.read_csv('data_5fold.csv')
subjects = data[data['slice']==0]

In [9]:
TRAIN_BATCH_SIZE = 64
VALID_BATCH_SIZE = 32
LR = 9e-5
EPOCHS = 120
device = torch.device('cuda')
verbose = False

In [ ]:
# 5 folds cross validation

for f in range(1) : 
    
    df_train = data[data['kfold'] !=f]
    df_valid = data[data['kfold'] ==f]
    Left_train_dataset = Merging_data_set(df_train, subjects, Left = True , is_train = True)
    Left_valid_dataset = Merging_data_set(df_valid, subjects, Left = True , is_train  = False)
    Left_model = UNet(1,1)
    Left_model = Left_model.to(device)
    val_loss , train_loss = run(Left_model, EPOCHS , Left_train_dataset , Left_valid_dataset,  TRAIN_BATCH_SIZE, VALID_BATCH_SIZE )  
    #torch.save(Left_model.state_dict(), f'Unet Left fold {f}.pt')


[get_training_augmentation]  resize_to: (160, 160)
--------- Epoch 0 ---------
 train_loss  = 0.5773016035556793
 val_loss  = 0.34039745330810545


In [ ]:
plt.plot(train_loss)
plt.plot(val_loss)
plt.title('Training on Left Hippocampus')
plt.ylabel('Loss')
plt.xlabel('Epoch')
plt.legend(['train', 'val'], loc='upper right')
plt.show()

In [ ]:
gc.collect()